In [ ]:
# install bark (make sure you have torch>=2 for much faster flash-attention)
!pip install git+https://github.com/suno-ai/bark.git

  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-kybuh55a
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-kybuh55a
  Resolved https://github.com/suno-ai/bark.git to commit 773624d26db84278a55aacae9a16d7b25fbccab8
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.8/135.8 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 36.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.4/11.4 MB 113.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.8/79.8 kB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 6.8 MB/s eta 0:00:00
  Created wheel for suno-bark: filename=suno_bark-0.0.1a0-py3-none-any.whl size=256

In [ ]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from scipy.io.wavfile import write as write_wav
import numpy as np
import random
from datetime import datetime
random.seed(datetime.now().timestamp())

from IPython.display import Audio

preload_models()

speakers_size = 9
P1 = "Tom Hanks"
P2 = "Billie Eilish"
r = random.randint(0, speakers_size)
speaker_lookup = {P1: f"v2/en_speaker_{r}", P2: f"v2/en_speaker_{r+1}", "Narrator":f"v2/en_speaker_{r+2}"}

def bark_TTS(script):
    script = script.strip().split("\n")
    script = [s.strip() for s in script if s]

    pieces = []
    silence = np.zeros(int(0.5*SAMPLE_RATE))
    prev_speaker = 0
    for line in script:
        speaker, text = line.split(": ")
        print(speaker, text)
        audio_array = generate_audio(text, history_prompt=speaker_lookup[speaker], )
        if(prev_speaker==speaker):
          pieces += [audio_array]
        else:
          pieces += [audio_array, silence.copy()]
        prev_speaker = speaker
    stitched_audio_array = np.concatenate(pieces)
    write_wav("bark_debate.wav", SAMPLE_RATE, stitched_audio_array)
    return stitched_audio_array


script1 = f"""
    Narrator: Elon Musk is a con-man
    {P1}: There are plenty of valid criticisms one can make of Elon Musk.  But I would argue the label con-man is not appropriate.
    {P2}: I'd argue that the good his companies do doesnt take anything away from his status as a con. he has directly lied to consumers multiple, *MULTIPLE* times.
    {P1}: For what it's worth, I know a few people that live in Brownsville, Texas where Space-X operates. They aren't fans of his politics.
    {P2}: I agree. That said, I would like Musk to stop wasting his time with Twitter and move some of his attention to another tangible benefit.
    {P1}: Would you say it's a fair assessment to claim these companies do great despite him, not because of him
"""

script = f"""
    Narrator: {P1} and {P2} will be debating that The Shoes off should be the default when visiting a guest’s house.
    {P1}: Hello my name is {P1} and I am for shoes off.
    {P2}: I am {P2} and I am against shoes off.
    {P1}: My only contribution is that IF you request that guests remove shoes, THEN you must have a seat by the front door so they can easily take them off or put them back on.
    {P2}: This is actually a great point I never considered. My brother in law and his wife are the only people I know who requires people to take off their shoes in their home.
    {P2}: But they literally have no furniture at all in their entryway so I have nowhere to place the kid I’m carrying and the bag I have but they always say
    {P2}: “remember to take of your shoes” as soon as you walk in. I find it annoying but it’s solely because of the inconvenience. If I could conveniently take off my shoes, I’d never even think about it.
    {P1}: I agree. We. Do this. We live in the country where lace up boots are the standard wear in winter.They aren't easy to put on and take off.
    {P2}: Yes of course, I totally agree with that and have such a stool.
    {P1}: lol what kind of mollycoddled demand is this? Maybe If you have a substantial entry area, but most people are perfectly capable of bending over or getting on one knee. Lazy!
"""
print(script)
audio = bark_TTS(script)
Audio(audio, rate=SAMPLE_RATE)


    Narrator: Tom Hanks and Billie Eilish will be debating that The Shoes off should be the default when visiting a guest’s house.
    Tom Hanks: Hello my name is Tom Hanks and I am for shoes off.
    Billie Eilish: I am Billie Eilish and I am against shoes off.
    Tom Hanks: My only contribution is that IF you request that guests remove shoes, THEN you must have a seat by the front door so they can easily take them off or put them back on.
    Billie Eilish: This is actually a great point I never considered. My brother in law and his wife are the only people I know who requires people to take off their shoes in their home. 
    Billie Eilish: But they literally have no furniture at all in their entryway so I have nowhere to place the kid I’m carrying and the bag I have but they always say 
    Billie Eilish: “remember to take of your shoes” as soon as you walk in. I find it annoying but it’s solely because of the inconvenience. If I could conveniently take off my shoes, I’d never ev

100%|██████████| 26/26 [00:24<00:00,  1.06it/s]


Tom Hanks Hello my name is Tom Hanks and I am for shoes off.


100%|██████████| 13/13 [00:12<00:00,  1.05it/s]


Billie Eilish I am Billie Eilish and I am against shoes off.


...

100%|██████████| 29/29 [00:26<00:00,  1.08it/s]


Billie Eilish Yes of course, I totally agree with that and have such a stool.


100%|██████████| 12/12 [00:10<00:00,  1.12it/s]


Tom Hanks lol what kind of mollycoddled demand is this? Maybe If you have a substantial entry area, but most people are perfectly capable of bending over or getting on one knee. Lazy!


100%|██████████| 33/33 [00:31<00:00,  1.06it/s]
